In [1]:
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import os
import plotly.io as pio

from scipy import special, stats

pio.templates.default = "plotly_white"
pio.renderers.default = os.environ.get("PLOTLY_RENDERER", "notebook")

np.set_printoptions(precision=6, suppress=True)
rng = np.random.default_rng(42)


In [2]:
def _check_loc_scale(loc: float, scale: float) -> None:
    if not (np.isfinite(loc) and np.isfinite(scale) and scale > 0):
        raise ValueError("Require finite loc and scale > 0.")


def semicircular_pdf(x, loc: float = 0.0, scale: float = 1.0):
    '''Semicircular pdf. Vectorized over x.'''
    _check_loc_scale(loc, scale)
    x = np.asarray(x, dtype=float)

    y = (x - loc) / scale
    out = np.zeros_like(y, dtype=float)

    inside = np.abs(y) <= 1.0
    out[inside] = (2.0 / (np.pi * scale)) * np.sqrt(np.clip(1.0 - y[inside] ** 2, 0.0, None))
    return out


def semicircular_cdf(x, loc: float = 0.0, scale: float = 1.0):
    '''Semicircular cdf. Vectorized over x.'''
    _check_loc_scale(loc, scale)
    x = np.asarray(x, dtype=float)

    y = (x - loc) / scale
    out = np.zeros_like(y, dtype=float)

    out[y >= 1.0] = 1.0

    mid = (y > -1.0) & (y < 1.0)
    ym = y[mid]
    out[mid] = 0.5 + (ym * np.sqrt(1.0 - ym**2) + np.arcsin(ym)) / np.pi
    return out


def semicircular_logpdf(x, loc: float = 0.0, scale: float = 1.0):
    '''Log-pdf. Returns -inf outside the support and at the endpoints.'''
    _check_loc_scale(loc, scale)
    x = np.asarray(x, dtype=float)

    y = (x - loc) / scale
    out = np.full_like(y, -np.inf, dtype=float)

    inside = np.abs(y) <= 1.0
    y_in = y[inside]

    out[inside] = np.log(2.0 / (np.pi * scale)) + 0.5 * np.log1p(-y_in**2)
    return out


def semicircular_rvs(size, loc: float = 0.0, scale: float = 1.0, rng=None):
    '''NumPy-only sampling via the "uniform disk" construction.'''
    _check_loc_scale(loc, scale)
    if rng is None:
        rng = np.random.default_rng()

    u = rng.random(size)
    theta = rng.random(size) * (2.0 * np.pi)
    r = np.sqrt(u)  # makes (r, theta) uniform over disk area

    return loc + scale * r * np.cos(theta)


In [3]:
from math import comb


def semicircular_mean(loc: float = 0.0, scale: float = 1.0) -> float:
    _check_loc_scale(loc, scale)
    return float(loc)


def semicircular_var(scale: float = 1.0) -> float:
    _check_loc_scale(0.0, scale)
    return float(scale**2 / 4.0)


def semicircular_excess_kurtosis() -> float:
    return -1.0


def catalan_number(n: int) -> int:
    if n < 0:
        raise ValueError("n must be >= 0")
    return comb(2 * n, n) // (n + 1)


def semicircular_central_moment_2n(n: int, scale: float = 1.0) -> float:
    '''E[(X-μ)^(2n)] for the semicircular distribution.'''
    _check_loc_scale(0.0, scale)
    return float(catalan_number(n) * (scale**2 / 4.0) ** n)


def semicircular_mgf(t, loc: float = 0.0, scale: float = 1.0):
    _check_loc_scale(loc, scale)
    t = np.asarray(t, dtype=float)
    z = scale * t

    # Stable handling near z=0
    ratio = np.where(np.abs(z) < 1e-12, 1.0 + z**2 / 8.0, 2.0 * special.i1(z) / z)
    return np.exp(loc * t) * ratio


def semicircular_cf(t, loc: float = 0.0, scale: float = 1.0):
    _check_loc_scale(loc, scale)
    t = np.asarray(t, dtype=float)
    z = scale * t

    ratio = np.where(np.abs(z) < 1e-12, 1.0 - z**2 / 8.0, 2.0 * special.j1(z) / z)
    return np.exp(1j * loc * t) * ratio


def semicircular_entropy(scale: float = 1.0) -> float:
    _check_loc_scale(0.0, scale)
    return float(np.log(np.pi * scale) - 0.5)


# Quick Monte Carlo sanity check
mu, R = 0.5, 2.0
x_mc = semicircular_rvs(250_000, loc=mu, scale=R, rng=rng)

print("MC mean :", x_mc.mean(), " | theory:", semicircular_mean(mu, R))
print("MC var  :", x_mc.var(), " | theory:", semicircular_var(R))
print("MC skew :", stats.skew(x_mc), " | theory: 0")
print("MC ex-k :", stats.kurtosis(x_mc, fisher=True), " | theory:", semicircular_excess_kurtosis())

# Entropy: compare our closed form to SciPy
print("entropy formula:", semicircular_entropy(R))
print("entropy SciPy  :", stats.semicircular.entropy(scale=R))

# Check the 4th central moment against Catalan formula (n=2)
mu4_mc = np.mean((x_mc - mu) ** 4)
mu4_th = semicircular_central_moment_2n(2, scale=R)
print("E[(X-μ)^4] MC:", mu4_mc, " | theory:", mu4_th)


MC mean : 0.49854065493504535  | theory: 0.5
MC var  : 1.0025105699993875  | theory: 1.0
MC skew : 0.0002972765510045654  | theory: 0
MC ex-k : -1.0034177602258956  | theory: -1.0
entropy formula: 1.3378770664093453
entropy SciPy  : 1.3378770664093453
E[(X-μ)^4] MC: 2.0066310114582215  | theory: 2.0


In [4]:
scales = [0.5, 1.0, 2.0]
locs = [0.0, 1.0]

fig = go.Figure()

for loc in locs:
    for scale in scales:
        x = np.linspace(loc - scale, loc + scale, 700)
        fig.add_trace(
            go.Scatter(
                x=x,
                y=semicircular_pdf(x, loc=loc, scale=scale),
                name=f"loc={loc:g}, scale={scale:g}",
            )
        )

fig.update_layout(
    title="Semicircular pdf: how loc and scale change the curve",
    xaxis_title="x",
    yaxis_title="density",
)
fig.show()


In [5]:
# Sampling demo
x_demo = semicircular_rvs(10, loc=0.0, scale=1.0, rng=rng)
x_demo


array([ 0.560276,  0.157799, -0.942746, -0.7539  , -0.73464 ,  0.511127,
       -0.158642,  0.243663, -0.867028, -0.499481])

In [6]:
mu, R = 0.0, 1.0
x = np.linspace(mu - R - 0.2, mu + R + 0.2, 1200)

pdf = semicircular_pdf(x, loc=mu, scale=R)
cdf = semicircular_cdf(x, loc=mu, scale=R)

fig_pdf = go.Figure(go.Scatter(x=x, y=pdf, name="pdf"))
fig_pdf.update_layout(title="Semicircular PDF (standard)", xaxis_title="x", yaxis_title="density")
fig_pdf.show()

fig_cdf = go.Figure(go.Scatter(x=x, y=cdf, name="cdf"))
fig_cdf.update_layout(title="Semicircular CDF (standard)", xaxis_title="x", yaxis_title="F(x)")
fig_cdf.show()

# Monte Carlo vs pdf
n = 80_000
s = semicircular_rvs(n, loc=mu, scale=R, rng=rng)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=s,
        nbinsx=70,
        histnorm="probability density",
        name="Monte Carlo",
        opacity=0.6,
    )
)
fig.add_trace(go.Scatter(x=x, y=pdf, name="theory pdf", line=dict(color="black")))
fig.update_layout(
    title="Monte Carlo samples vs semicircular pdf",
    xaxis_title="x",
    yaxis_title="density",
    barmode="overlay",
)
fig.show()


In [7]:
mu, R = 1.25, 0.8
x = np.linspace(mu - R, mu + R, 800)

pdf_ours = semicircular_pdf(x, loc=mu, scale=R)
pdf_scipy = stats.semicircular.pdf(x, loc=mu, scale=R)

cdf_ours = semicircular_cdf(x, loc=mu, scale=R)
cdf_scipy = stats.semicircular.cdf(x, loc=mu, scale=R)

print("max |pdf diff|:", np.max(np.abs(pdf_ours - pdf_scipy)))
print("max |cdf diff|:", np.max(np.abs(cdf_ours - cdf_scipy)))

# Sampling + fitting
true_loc, true_scale = -0.5, 1.7
sample = stats.semicircular.rvs(loc=true_loc, scale=true_scale, size=2500, random_state=rng)
loc_hat, scale_hat = stats.semicircular.fit(sample)

print("true loc, scale:", true_loc, true_scale)
print("fit  loc, scale:", loc_hat, scale_hat)


max |pdf diff|: 2.220446049250313e-16
max |cdf diff|: 1.1102230246251565e-16
true loc, scale: -0.5 1.7
fit  loc, scale: -0.5069591823846296 1.698045426706722


In [8]:
mu, R = 0.2, 1.3
n = 600

x_semi = stats.semicircular.rvs(loc=mu, scale=R, size=n, random_state=rng)
x_unif = stats.uniform.rvs(loc=mu - R, scale=2 * R, size=n, random_state=rng)

ks_semi = stats.kstest(x_semi, "semicircular", args=(mu, R))
ks_unif = stats.kstest(x_unif, "semicircular", args=(mu, R))

print("KS (true semicircular) statistic:", ks_semi.statistic, "p:", ks_semi.pvalue)
print("KS (uniform)           statistic:", ks_unif.statistic, "p:", ks_unif.pvalue)

x_grid = np.linspace(mu - R, mu + R, 800)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=x_semi,
        nbinsx=55,
        histnorm="probability density",
        name="data: semicircular",
        opacity=0.55,
    )
)
fig.add_trace(
    go.Histogram(
        x=x_unif,
        nbinsx=55,
        histnorm="probability density",
        name="data: uniform",
        opacity=0.40,
    )
)
fig.add_trace(
    go.Scatter(
        x=x_grid,
        y=stats.semicircular.pdf(x_grid, loc=mu, scale=R),
        name="semicircular pdf (H0)",
        line=dict(color="black"),
    )
)
fig.update_layout(
    title="Goodness-of-fit intuition: semicircular vs uniform data",
    xaxis_title="x",
    yaxis_title="density",
    barmode="overlay",
)
fig.show()


KS (true semicircular) statistic: 0.04323935373187415 p: 0.20588329780325731
KS (uniform)           statistic: 0.06402741241309892 p: 0.013958570716509898


In [9]:
def _normalize_on_grid(grid, log_unnorm_density):
    log_unnorm_density = np.asarray(log_unnorm_density, dtype=float)
    log_unnorm_density = log_unnorm_density - np.max(log_unnorm_density)
    un = np.exp(log_unnorm_density)
    z = np.trapz(un, grid)
    return un / z


# Model: y_i | theta ~ Normal(theta, sigma_obs^2)
mu, R = 0.0, 1.0
sigma_obs = 0.35
n = 25

theta_true = 0.25
y = theta_true + rng.normal(scale=sigma_obs, size=n)

# Grid on the support
grid = np.linspace(mu - R, mu + R, 2001)

# Log-likelihood up to a constant
loglike = -0.5 * np.sum(((y[:, None] - grid[None, :]) / sigma_obs) ** 2, axis=0)

# Priors
logprior_uniform = np.zeros_like(grid)
logprior_uniform[(grid < mu - R) | (grid > mu + R)] = -np.inf

logprior_semi = semicircular_logpdf(grid, loc=mu, scale=R)

post_uniform = _normalize_on_grid(grid, loglike + logprior_uniform)
post_semi = _normalize_on_grid(grid, loglike + logprior_semi)

mean_uniform = np.trapz(grid * post_uniform, grid)
mean_semi = np.trapz(grid * post_semi, grid)

fig = go.Figure()
fig.add_trace(go.Scatter(x=grid, y=post_uniform, name=f"posterior (uniform prior), mean={mean_uniform:.3f}"))
fig.add_trace(go.Scatter(x=grid, y=post_semi, name=f"posterior (semicircular prior), mean={mean_semi:.3f}"))
fig.add_vline(x=theta_true, line=dict(color="black", dash="dot"), annotation_text="true θ")

fig.update_layout(
    title="Bayesian example: uniform vs semicircular prior on a bounded θ",
    xaxis_title="θ",
    yaxis_title="posterior density",
)
fig.show()


/tmp/ipykernel_1034072/1049027462.py:46: RuntimeWarning:

divide by zero encountered in log1p



In [10]:
n = 250
A = rng.normal(size=(n, n))
W = np.triu(A)
W = W + W.T - np.diag(np.diag(W))
W = W / np.sqrt(n)

eigvals = np.linalg.eigvalsh(W)

x = np.linspace(-2.2, 2.2, 900)
pdf = stats.semicircular.pdf(x, loc=0.0, scale=2.0)

fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=eigvals,
        nbinsx=60,
        histnorm="probability density",
        name="eigenvalues",
        opacity=0.65,
    )
)
fig.add_trace(go.Scatter(x=x, y=pdf, name="semicircle pdf (scale=2)", line=dict(color="black")))
fig.update_layout(
    title="Wigner semicircle law (simulation)",
    xaxis_title="eigenvalue",
    yaxis_title="density",
    barmode="overlay",
)
fig.show()

print("eigenvalue range:", (eigvals.min(), eigvals.max()))


eigenvalue range: (-1.930360346008193, 1.9533443905131391)
